In [1]:
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt 
import scipy.sparse as sp
import tensorflow as tf
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from tqdm import tqdm
import keras
from sklearn.model_selection import train_test_split

Using TensorFlow backend.


In [2]:
data = pd.read_csv("u.data", sep ="\t" , header = None ).sort_values([0,3]).reset_index(drop = True)

In [3]:
data[0] = data[0] - 1
data[1] = data[1] - 1

In [4]:
user_p = pd.read_csv("u.user" , sep = "|"  ,header = None)

In [5]:
user_p = user_p.drop(columns = [0])

In [6]:
user_p[2] = pd.Categorical(user_p[2]).codes

In [7]:
user_p[3] = pd.Categorical(user_p[3]).codes

In [8]:
user_p = user_p.drop(columns = 4)

In [9]:
mat_x = sp.lil_matrix((943,1682) , dtype = np.int8)
mat_y = sp.lil_matrix((943,1682) , dtype = np.int8)

In [10]:
user_num = 943
item_num = 1682

In [11]:
for i in tqdm(range(user_num)):
    u = data[data[0] == i]
    limit = int(u.shape[0]*0.8)
#     print(u.head())
#     print(u.iloc[0])
    for j in range(u.shape[0]):
        row = u.iloc[j][0]
        col = u.iloc[j][1]
        rate =u.iloc[j][2]
        if j < limit:
            mat_x[row,col] = rate
        else:
            mat_y[row,col] = rate
#     break

100%|████████████████████████████████████████| 943/943 [00:44<00:00, 21.29it/s]


In [12]:
user_p.columns = ["age" , "gender" , "job"]

In [13]:
user_p.head() 

age  gender  job
0   24       1   19
1   53       0   13
2   23       1   20
3   24       1   19
4   33       0   13

In [140]:
 ggg = np.mean(((mat_x + mat_y)!= 0) ,axis = 1)

In [138]:
len(ggg)

943

In [142]:
user_p

array([[ 0,  1, 19],
       [ 2,  0, 13],
       [ 0,  1, 20],
       ...,
       [ 0,  1, 18],
       [ 1,  0, 10],
       [ 0,  1, 18]], dtype=int32)

In [14]:
a = []
for i in user_p.age :
    if i >= 50 :
        a.append(2)
    elif (i < 50) & (25< i):
        a.append(1)
    else:
        a. append(0)

In [15]:
user_p.age = np.array(a)

In [16]:
user_p = np.array(user_p)

In [17]:
age_p = keras.utils.np_utils.to_categorical(user_p[:,0],3)

In [18]:
gender_p = keras.utils.np_utils.to_categorical(user_p[:,1],2)

In [19]:
jobs_p = keras.utils.np_utils.to_categorical(user_p[:,2],21)

In [20]:
mat_x = mat_x.toarray()
mat_y = mat_y.toarray()

In [21]:
kfold = KFold(5 , shuffle= True)

In [22]:
item_x = mat_x.transpose()
item_y = mat_y.transpose()

In [121]:
user_p

array([[ 0,  1, 19],
       [ 2,  0, 13],
       [ 0,  1, 20],
       ...,
       [ 0,  1, 18],
       [ 1,  0, 10],
       [ 0,  1, 18]], dtype=int32)

In [24]:
user = tf.placeholder(tf.float32, [None,1682])

item_i = tf.placeholder(tf.float32 , [None,943])

item_j = tf.placeholder(tf.float32 , [None,943])

ground_truth = tf.placeholder(tf.float32, [None ,1])

y_truth_age = tf.placeholder(tf.int32,[None,3])

y_truth_job = tf.placeholder(tf.int32,[None ,21])

y_truth_gender = tf.placeholder(tf.int32,[None ,2])

### set 

w1 = tf.get_variable('w1',shape=[1682, 256],initializer=tf.glorot_uniform_initializer())

b1 = tf.get_variable('b1',shape=[256],initializer=tf.zeros_initializer)

w2 = tf.get_variable('w2',shape=[943, 256],initializer=tf.glorot_uniform_initializer())

b2 = tf.get_variable('b2',shape=[256],initializer=tf.zeros_initializer)

w3 = tf.get_variable('w3',shape=[943, 256],initializer=tf.glorot_uniform_initializer())

b3 = tf.get_variable('b3',shape=[256],initializer=tf.zeros_initializer)

##user embedding
h1 = tf.matmul(user, w1) + b1

user_embedding = tf.sigmoid(h1)
##item_i embedding
h2 = tf.matmul(item_i, w2) + b2

item_i_embedding = tf.sigmoid(h2)

##item_j embedding
h3 = tf.matmul(item_j, w3) + b3

item_j_embedding = tf.sigmoid(h3)
###

w4 = tf.get_variable('w4',shape=[256, 32],initializer=tf.glorot_uniform_initializer())

b4 = tf.get_variable('b4',shape=[32],initializer=tf.zeros_initializer)
###User part
h4 = tf.matmul(user_embedding, w4) + b4

user_v = tf.nn.leaky_relu(h4)

### item_i part
h5 = tf.matmul(item_i_embedding, w4) + b4

item_i_v = tf.nn.leaky_relu(h5)

### item_j part
h6 = tf.matmul(item_j_embedding, w4) + b4

item_j_v = tf.nn.leaky_relu(h6)

### concat them and 
i_v = tf.concat([user_v , item_i_v] ,axis = 1 )

j_v = tf.concat([user_v , item_j_v] ,axis = 1 )

### they both share the same  (w and b)

w5 = tf.get_variable('w5',shape=[64, 1],initializer=tf.glorot_uniform_initializer())

b5 = tf.get_variable('b5',shape=[1],initializer=tf.zeros_initializer)

### i part

h7 = tf.matmul(i_v, w5) + b5

output_i = tf.nn.leaky_relu(h7)

### j part 

h8 = tf.matmul(j_v, w5) + b5

output_j = tf.nn.leaky_relu(h8)

### loss function part1 recomender

regulars1 = tf.nn.l2_loss(w1) + tf.nn.l2_loss(w2) + tf.nn.l2_loss(w3) + tf.nn.l2_loss(w4) + tf.nn.l2_loss(w5)

regulars2 = tf.nn.l2_loss(b1) + tf.nn.l2_loss(b2) + tf.nn.l2_loss(b3) + tf.nn.l2_loss(b4) + tf.nn.l2_loss(b5)

loss_function =  tf.reduce_mean(- tf.log(tf.sigmoid(tf.multiply(tf.subtract(output_i , output_j) , ground_truth )))) + regulars1 +regulars2

predict = 0.5 *(output_i + output_j)

### predict

###predict
rnn_input = tf.reshape(tensor = item_i_embedding , shape = (1, -1 , 256))

rnn_output = tf.reshape(keras.layers.SimpleRNN(128)(keras.layers.Input(tensor = rnn_input)) ,(-1,128))

final = tf.concat([rnn_output , user_embedding] ,axis = 1)

split1 , split2 , split3 = tf.split(final,[128 , 128 ,128 ] ,1)

w6 = tf.get_variable('w6',shape=[128, 21],initializer=tf.glorot_uniform_initializer())

b6 = tf.get_variable('b6',shape=[21],initializer=tf.zeros_initializer)

w7 = tf.get_variable('w7',shape=[128, 2],initializer=tf.glorot_uniform_initializer())

b7 = tf.get_variable('b7',shape=[2],initializer=tf.zeros_initializer)

w8 = tf.get_variable('w8',shape=[128, 3],initializer=tf.glorot_uniform_initializer())

b8 = tf.get_variable('b8',shape=[3],initializer=tf.zeros_initializer)

y_job = tf.matmul(split1, w6) + b6

y_gender = tf.matmul(split2, w7) + b7 

y_age = tf.matmul(split3, w8) + b8 

regulars3 = tf.nn.l2_loss(w6) + tf.nn.l2_loss(b6) + tf.nn.l2_loss(w7) + tf.nn.l2_loss(b7) + tf.nn.l2_loss(w8) + tf.nn.l2_loss(b8)

cross_entropy_job =tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_truth_job, logits=y_job))

cross_entropy_gender =tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_truth_gender, logits=y_gender))

cross_entropy_age =tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_truth_age, logits=y_age))

attacker_total_loss = cross_entropy_age + cross_entropy_gender + cross_entropy_job + regulars3

total_loss = loss_function - 0.5 * attacker_total_loss

train_step_recommander = tf.train.AdamOptimizer().minimize(total_loss , var_list = [w1,w2,w3,w4,w5,b1,b2,b3,b4,b5])

train_step_attacker = tf.train.AdamOptimizer().minimize(attacker_total_loss , var_list = [w6,w7,w8,b6,b7,b8])

sess = tf.InteractiveSession()

tf.global_variables_initializer().run()

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.

Instructions for updating:
Use tf.cast instead.


In [43]:
def step1():
    for index  in tqdm(use_index):
        ### train the recommender 
        input_user = X_train[index].reshape(1,-1)
        positve_sample = (np.where(X_train[index] != 0)[0])
        negaitve_sample = (np.where(X_train[index] == 0)[0])
        rated_sample = np.where(ground_X_train[index][negaitve_sample] != 0)[0]
        unrated_sample = np.where(ground_X_train[index][negaitve_sample] == 0)[0]
        use_unrated_sample = np.random.choice(unrated_sample ,replace = False , size = 2* len(rated_sample))
        final_use = np.append(rated_sample ,use_unrated_sample)
        ### 對於每一個user看未來有幾個是真的有評過分的，取這個樣本數的四倍平過的所以總共迭代為
        ###(user(200) * train中有評過的(positive_sample) * ((train中沒評過但後來有評過分的) + (train中沒評過但後來沒有評過分的 ,取四倍)))
    #     break
        for j in positve_sample:
            for k in final_use:
                input_item_i = item_x[j].reshape(1,-1)
                input_item_j = item_x[k].reshape(1,-1)
                if  X_train[index][j] >  ground_X_train[index][k]:
                    input_ground_truth = np.array(1).reshape(1,-1)
                else:
                    input_ground_truth = np.array(-1).reshape(1,-1)
#             break
#         break
#     break
    #             print(input_user.shape)
    #             print(input_item_i.shape)
    #             print(input_item_j.shape)
    #             print(input_ground_truth.shape)
                sess.run(loss_function , feed_dict={user:input_user ,item_i:input_item_i ,item_j:input_item_j,ground_truth:input_ground_truth})

In [44]:
def step2():
    for index  in tqdm(use_index):
        ### train the recommender 
        input_user = X_train[index].reshape(1,-1)
        positve_sample = (np.where(X_train[index] != 0)[0])
        negaitve_sample = (np.where(X_train[index] == 0)[0])
        ### because train this is impossible
        ### I only train 4 * positive_sample
        a = np.array([])
        for j in negaitve_sample:
            input_item_i = item_x[j].reshape(1,-1)
            input_item_j = item_x[j].reshape(1,-1)
            res =  sess.run(predict, feed_dict={user:input_user ,item_i:input_item_i ,item_j:input_item_j})
            a = np.append(a , res[0,0])
        recommend_sample = a.argsort()[-20:]
        input_item_i = item_x[np.append(positve_sample , recommend_sample)].reshape(-1,943)
        input_y_age = age_p[index].reshape(-1,3)
        input_y_gender = gender_p[index].reshape(-1,2)
        input_y_job =  jobs_p[index].reshape(-1,21)
        sess.run(train_step_attacker ,  feed_dict={user:input_user ,item_i:input_item_i ,y_truth_age:input_y_age ,y_truth_gender:input_y_gender ,y_truth_job :input_y_job})

In [45]:
for zz in tqdm(range(100)):
    mini_batch_size  = 200
    use_index = np.random.choice(range(X_train.shape[0]) , size = mini_batch_size, replace = False)
    step1()
    step2()



  0%|                                                  | 0/100 [00:00<?, ?it/s]


  0%|                                                  | 0/200 [00:00<?, ?it/s]


  0%|▏                                         | 1/200 [00:01<03:51,  1.16s/it]


  1%|▍                                         | 2/200 [00:39<40:40, 12.32s/it]


  2%|▋                                         | 3/200 [00:54<43:06, 13.13s/it]


  2%|▊                                         | 4/200 [01:17<52:41, 16.13s/it]


  2%|█                                         | 5/200 [01:17<36:57, 11.37s/it]


  3%|█▎                                        | 6/200 [01:18<26:08,  8.09s/it]


  4%|█▍                                        | 7/200 [01:23<23:14,  7.23s/it]


  4%|█▋                                        | 8/200 [01:53<45:01, 14.07s/it]


  4%|█▉                                        | 9/200 [01:55<33:12, 10.43s/it]


  5%|██                                       | 10/200 [02:04<31:35,  9.98s/it]


  6%|██▎      

 49%|████████████████████                     | 98/200 [16:48<32:11, 18.93s/it]


 50%|████████████████████▎                    | 99/200 [16:51<23:35, 14.02s/it]


 50%|████████████████████                    | 100/200 [16:57<19:31, 11.71s/it]


 50%|████████████████████▏                   | 101/200 [16:58<14:11,  8.60s/it]


 51%|████████████████████▍                   | 102/200 [17:02<11:31,  7.05s/it]


 52%|████████████████████▌                   | 103/200 [17:02<08:10,  5.06s/it]


 52%|████████████████████▊                   | 104/200 [17:02<05:46,  3.61s/it]


 52%|█████████████████████                   | 105/200 [17:17<10:48,  6.83s/it]


 53%|█████████████████████▏                  | 106/200 [17:43<20:05, 12.82s/it]


 54%|████████████████████▎                 | 107/200 [21:55<2:11:04, 84.57s/it]


 54%|████████████████████▌                 | 108/200 [22:02<1:33:40, 61.09s/it]


 55%|████████████████████▋                 | 109/200 [22:04<1:06:01, 43.54s/it]


 55%|███████████

 98%|███████████████████████████████████████▍| 197/200 [45:58<01:05, 21.69s/it]


 99%|███████████████████████████████████████▌| 198/200 [45:59<00:31, 15.50s/it]


100%|███████████████████████████████████████▊| 199/200 [47:20<00:35, 35.30s/it]


100%|████████████████████████████████████████| 200/200 [47:21<00:00, 24.82s/it]


  0%|                                                  | 0/200 [00:00<?, ?it/s]


  0%|▏                                         | 1/200 [00:01<04:14,  1.28s/it]


  1%|▍                                         | 2/200 [00:02<04:05,  1.24s/it]


  2%|▋                                         | 3/200 [00:03<04:01,  1.23s/it]


  2%|▊                                         | 4/200 [00:04<03:57,  1.21s/it]


  2%|█                                         | 5/200 [00:06<04:03,  1.25s/it]


  3%|█▎                                        | 6/200 [00:07<04:03,  1.26s/it]


  4%|█▍                                        | 7/200 [00:08<04:01,  1.25s/it]


  4%|█▋         

 48%|███████████████████▍                     | 95/200 [02:01<02:10,  1.24s/it]


 48%|███████████████████▋                     | 96/200 [02:02<02:11,  1.26s/it]


 48%|███████████████████▉                     | 97/200 [02:04<02:05,  1.21s/it]


 49%|████████████████████                     | 98/200 [02:05<02:04,  1.22s/it]


 50%|████████████████████▎                    | 99/200 [02:06<02:04,  1.23s/it]


 50%|████████████████████                    | 100/200 [02:07<02:03,  1.23s/it]


 50%|████████████████████▏                   | 101/200 [02:09<02:04,  1.25s/it]


 51%|████████████████████▍                   | 102/200 [02:10<02:02,  1.25s/it]


 52%|████████████████████▌                   | 103/200 [02:11<02:02,  1.26s/it]


 52%|████████████████████▊                   | 104/200 [02:12<02:01,  1.27s/it]


 52%|█████████████████████                   | 105/200 [02:14<01:59,  1.26s/it]


 53%|█████████████████████▏                  | 106/200 [02:15<01:55,  1.23s/it]


 54%|███████████

 97%|██████████████████████████████████████▊ | 194/200 [04:05<00:07,  1.23s/it]


 98%|███████████████████████████████████████ | 195/200 [04:07<00:06,  1.25s/it]


 98%|███████████████████████████████████████▏| 196/200 [04:08<00:05,  1.28s/it]


 98%|███████████████████████████████████████▍| 197/200 [04:09<00:03,  1.23s/it]


 99%|███████████████████████████████████████▌| 198/200 [04:10<00:02,  1.24s/it]


100%|███████████████████████████████████████▊| 199/200 [04:11<00:01,  1.19s/it]


100%|████████████████████████████████████████| 200/200 [04:13<00:00,  1.22s/it]

  1%|▎                                    | 1/100 [51:34<85:05:43, 3094.38s/it]


  0%|                                                  | 0/200 [00:00<?, ?it/s]


  0%|▏                                         | 1/200 [00:00<01:46,  1.86it/s]


  1%|▍                                       | 2/200 [05:05<5:03:06, 91.85s/it]


  2%|▌                                       | 3/200 [05:05<3:31:23, 64.38s/it]


  2%|▊           

...

 99%|███████████████████████████████████▋| 99/100 [73:53:47<47:43, 2863.62s/it]


  0%|                                                  | 0/200 [00:00<?, ?it/s]


  0%|▏                                         | 1/200 [00:04<15:06,  4.56s/it]


  1%|▍                                         | 2/200 [00:10<15:58,  4.84s/it]


  2%|▋                                         | 3/200 [00:18<19:36,  5.97s/it]


  2%|▊                                         | 4/200 [00:20<15:04,  4.62s/it]


  2%|█                                         | 5/200 [00:48<38:14, 11.77s/it]


  3%|█▎                                        | 6/200 [00:48<26:50,  8.30s/it]


  4%|█▍                                      | 7/200 [01:41<1:09:27, 21.59s/it]


  4%|█▋                                        | 8/200 [01:42<49:08, 15.36s/it]


  4%|█▉                                        | 9/200 [01:53<45:24, 14.26s/it]


  5%|██                                       | 10/200 [01:54<32:10, 10.16s/it]


  6%|██▎        

 49%|████████████████████                     | 98/200 [15:13<31:33, 18.56s/it]


 50%|████████████████████▎                    | 99/200 [15:13<21:59, 13.06s/it]


 50%|████████████████████                    | 100/200 [15:45<31:23, 18.83s/it]


 50%|████████████████████▏                   | 101/200 [15:50<24:19, 14.74s/it]


 51%|████████████████████▍                   | 102/200 [15:51<17:00, 10.42s/it]


 52%|████████████████████▌                   | 103/200 [15:51<11:59,  7.41s/it]


 52%|████████████████████▊                   | 104/200 [16:04<14:37,  9.14s/it]


 52%|█████████████████████                   | 105/200 [16:05<10:24,  6.58s/it]


 53%|█████████████████████▏                  | 106/200 [16:06<07:41,  4.91s/it]


 54%|█████████████████████▍                  | 107/200 [16:10<07:03,  4.55s/it]


 54%|█████████████████████▌                  | 108/200 [16:13<06:32,  4.26s/it]


 55%|█████████████████████▊                  | 109/200 [16:17<06:08,  4.05s/it]


 55%|███████████

 98%|███████████████████████████████████████▍| 197/200 [36:47<00:47, 15.81s/it]


 99%|███████████████████████████████████████▌| 198/200 [36:52<00:25, 12.54s/it]


100%|███████████████████████████████████████▊| 199/200 [37:33<00:21, 21.02s/it]


100%|████████████████████████████████████████| 200/200 [37:33<00:00, 14.91s/it]


  0%|                                                  | 0/200 [00:00<?, ?it/s]


  0%|▏                                         | 1/200 [00:01<04:39,  1.41s/it]


  1%|▍                                         | 2/200 [00:03<04:51,  1.47s/it]


  2%|▋                                         | 3/200 [00:04<05:17,  1.61s/it]


  2%|▊                                         | 4/200 [00:06<05:13,  1.60s/it]


  2%|█                                         | 5/200 [00:07<04:59,  1.53s/it]


  3%|█▎                                        | 6/200 [00:09<04:59,  1.55s/it]


  4%|█▍                                        | 7/200 [00:11<04:57,  1.54s/it]


  4%|█▋         

 48%|███████████████████▍                     | 95/200 [02:29<02:55,  1.67s/it]


 48%|███████████████████▋                     | 96/200 [02:30<02:45,  1.59s/it]


 48%|███████████████████▉                     | 97/200 [02:31<02:39,  1.55s/it]


 49%|████████████████████                     | 98/200 [02:33<02:36,  1.53s/it]


 50%|████████████████████▎                    | 99/200 [02:34<02:32,  1.51s/it]


 50%|████████████████████                    | 100/200 [02:36<02:25,  1.45s/it]


 50%|████████████████████▏                   | 101/200 [02:37<02:24,  1.46s/it]


 51%|████████████████████▍                   | 102/200 [02:39<02:23,  1.46s/it]


 52%|████████████████████▌                   | 103/200 [02:40<02:30,  1.55s/it]


 52%|████████████████████▊                   | 104/200 [02:42<02:27,  1.53s/it]


 52%|█████████████████████                   | 105/200 [02:43<02:26,  1.54s/it]


 53%|█████████████████████▏                  | 106/200 [02:45<02:24,  1.54s/it]


 54%|███████████

 97%|██████████████████████████████████████▊ | 194/200 [05:06<00:09,  1.66s/it]


 98%|███████████████████████████████████████ | 195/200 [05:08<00:08,  1.71s/it]


 98%|███████████████████████████████████████▏| 196/200 [05:10<00:07,  1.75s/it]


 98%|███████████████████████████████████████▍| 197/200 [05:12<00:05,  1.75s/it]


 99%|███████████████████████████████████████▌| 198/200 [05:14<00:03,  1.75s/it]


100%|███████████████████████████████████████▊| 199/200 [05:15<00:01,  1.70s/it]


100%|████████████████████████████████████████| 200/200 [05:17<00:00,  1.77s/it]

100%|███████████████████████████████████| 100/100 [74:36:38<00:00, 2775.96s/it]

In [59]:
X_test.shape

(189, 1682)

In [96]:
ground_X_test.shape

(189, 1682)

In [57]:
saver.save(sess, './my_model/my_test_model')

'./my_model/my_test_model'

In [97]:
ground_X_test[1]

array([0, 4, 0, ..., 0, 0, 0], dtype=int8)

In [102]:
for j in np.where(X_test[1] == 0)[0]:
    input_item_i = item_x[j].reshape(1,-1)
    input_item_j = item_x[j].reshape(1,-1)
    res =  sess.run(predict, feed_dict={user:input_user ,item_i:input_item_i ,item_j:input_item_j})
    a = np.append(a , res[0,0])

In [120]:
set(a.argsort()[-100:]) & set(ground_X_test[1].argsort()[-100:])

{1, 547, 551, 565, 601, 789}

In [117]:
ground_X_test[1].argsort()[-20:]

array([  75,  823,    1,  789,  692, 1064,  630,  549,  577,  185,  658,
       1216,  818,  760,  720, 1466,  832,  160, 1013,  650], dtype=int64)